In [1]:
# instalar: pip install liac-arff
import arff
import pandas as pd
import numpy as np 
import random
import imblearn
from imblearn.under_sampling import RandomUnderSampler
from sklearn import svm
from sklearn.metrics import precision_score, accuracy_score, classification_report, f1_score, recall_score, confusion_matrix
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from csv import DictReader
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import GridSearchCV, train_test_split, StratifiedKFold
import seaborn as sns
import matplotlib.pyplot as plt
# import tensorflow as tf
# from tensorflow import keras
# from tensorflow.keras import layers

### Atributos dos datasets

**Cada atributo pode conter 2 ou 3 valores, sendo esses:**
* -1: Phishing;
*  1: Legítimo;
*  0: Suspeito;

____

0 @relation phishing

02 @attribute having_IP_Address   { -1,1 } <br>
03 @attribute URL_Length          { 1,0,-1 } <br>
04 @attribute Shortining_Service  { 1,-1 } <br>
05 @attribute having_At_Symbol    { 1,-1 } <br>
06 @attribute double_slash_redirecting { -1,1 } <br>
07 @attribute Prefix_Suffix       { -1,1 } <br>
08 @attribute having_Sub_Domain   { -1,0,1 } <br>
09 @attribute SSLfinal_State      { -1,1,0 } <br>
10 @attribute Domain_registeration_length { -1,1 } <br>
11 @attribute Favicon     { 1,-1 } <br>
12 @attribute port        { 1,-1 } <br>
13 @attribute HTTPS_token { -1,1 } <br>
14 @attribute Request_URL { 1,-1 } <br>
15 @attribute URL_of_Anchor { -1,0,1 } <br>
16 @attribute Links_in_tags { 1,-1,0 } <br>
17 @attribute SFH  { -1,1,0 } <br>
18 @attribute Submitting_to_email { -1,1 } <br>
19 @attribute Abnormal_URL        { -1,1 } <br>
20 @attribute Redirect      { 0,1 } <br>
21 @attribute on_mouseover  { 1,-1 } <br>
22 @attribute RightClick    { 1,-1 } <br>
23 @attribute popUpWidnow   { 1,-1 } <br>
24 @attribute Iframe { 1,-1 } <br>
25 @attribute age_of_domain { -1,1 } <br>
26 @attribute DNSRecord     { -1,1 } <br>
27 @attribute web_traffic   { -1,0,1 } <br>
28 @attribute Page_Rank     { -1,1 } <br>
29 @attribute Google_Index  { 1,-1 } <br>
30 @attribute Links_pointing_to_page { 1,0,-1 } <br>
31 @attribute Statistical_report     { -1,1 } <br>
32 @attribute Result    { -1,1 } <br>

**Limpeza dos dados, a tabela a seguir mostra os atributos selecionados do dataset 1:**

| **#** | **Attributes**              | **Description**                                                      | **Feature Type** |
|-------|-----------------------------|----------------------------------------------------------------------|------------------|
| 1     | having_IP_Address           | If the domain part has an IP address                                 | Lexical          |
| 2     | URL_Length                  | Number of characters in the URL                                      | Lexical          |
| 3     | Shortining_Service          | Is the URL shortened                                                 | Lexical          |
| 4     | having_At_Symbol            | Is “@” sign present                                                  | Lexical          |
| 5     | Prefix_Suffix               | Does the domain part include “-* symbol  (separates suffix prefix)   | Lexical          |
| 6     | having_Sub_Domain           | Is the number of sub-domains high  (greater than 2)                  | Lexical          |
| 7     | SSLfinal_State              | Has valid SSL certificate (age)                                      | Domain           |
| 8     | Domain_registeration_length | Is the domain age of the website short (shorter than a year)         | Domain           |
| 9     | Request_URL                 | Are the external objects (images, videos) loaded from another domain | Content          |
| 10    | URL_of_Anchor               | Is the URL anchor linking to a webpage                               | Content          |
| 11    | Links_in_tags               | Presence of \<meta\>, \<scripts\>,  \<link\> tags                          | Content          |
| 12    | SFH                         | Does the server form handler(SFH) contain empty strings              | Domain           |
| 13    | Abnormal_URL                | Is the hostname included in WHOIS database                           | Lexical          |
| 14    | age_of_domain               | Is the age of the website short or long                              | Domain           |
| 15    | DNSRecord                   | If the website is recognized by WHOIS database                       | Domain           |
| 16    | web_traffic                 | If the webpage is frequently visited                                 | Domain           |
| 17    | Page_Rank                   | How important the webpage is on the internet                         | Domain           |
| 18    | Google_Index                | If the website is in Google’s index or not                           | Domain           |
| 19    | Statistical_report          | If the host belongs to top phishing  IPs or domains (PhishTank)      | Domain           |
___

**Atributos adicionais no segundo dataset:**

| **#** | **Attributes**              | **Description**                                                      | **Feature Type** |
|-------|-----------------------------|----------------------------------------------------------------------|------------------|
| 1     | external_objects            | Any suspicious behaviors related to website elements                               | Content          |
| 2     | anchor_tags                 | Any suspicious behaviors related to the anchor tag                                 | Content          |
____

**Por fim temos os atributos de cada dataset:**

| **#** | **Attributes**              | **Presence of these features in the datasets** |
|-------|-----------------------------|------------------------------------------------|
| 1     | having_IP_Address           | Both                                           |
| 2     | URL_Length                  | Both                                           |
| 3     | Shortining_Service          | Both                                           |
| 4     | having_At_Symbol            | Both                                           |
| 5     | Prefix_Suffix               | Both                                           |
| 6     | having_Sub_Domain           | Both                                           |
| 7     | SSLfinal_State              | Both                                           |
| 8     | Domain_registeration_length | Both                                           |
| 9     | Links_in_tags               | Both                                           |
| 10    | SFH                         | Both                                           |
| 11    | Abnormal_URL                | Both                                           |
| 12    | age_of_domain               | Both                                           |
| 13    | DNSRecord                   | Both                                           |
| 14    | web_traffic                 | Both                                           |
| 15    | Statistical_report          | Both                                           |
| 16    | Request_URL                 | First dataset                                  |
| 17    | URL_of_Anchor               | First dataset                                  |
| 18    | Page_Rank                   | First dataset                                  |
| 19    | Google_Index                | First dataset                                  |
| 20    | external_objects            | Second dataset                                 |
| 21    | anchor_tags                 | Second dataset                                 |

In [9]:
# file_path = "trainingdataset.arff" # Dados: 11055

# Abrir o arquivo ARFF
with open("trainingdataset.arff", 'r') as file:
    arff_data = arff.load(file)

# Acessar os dados do arquivo
data = arff_data['data']  # Dados em formato de lista ou matriz
attributes = arff_data['attributes']  # Atributos do arquivo ARFF

ST_df = pd.DataFrame(data, columns=[attr[0] for attr in attributes])

oversample1 = RandomUnderSampler(sampling_strategy='majority')

ST_df['Result'] = ST_df['Result'].astype(int)

ST_df_best_features = ST_df.drop([
    'double_slash_redirecting', 
    'Favicon', 
    'port', 
    'HTTPS_token', 
    'Submitting_to_email', 
    'Redirect', 
    'on_mouseover', 
    'RightClick',
    'popUpWidnow', 
    'Iframe', 
    'Links_pointing_to_page'
], axis=1)


# Analise de correlação dos atributos, utilizando o método de Pearson
ST_df_corr = ST_df.corr(method = 'pearson')

plt.figure(figsize=(16,16), dpi =1000)
sns.heatmap(ST_df_corr,annot=True,fmt=".2f", linewidth=.5)
plt.show()

# ST_df_best_features

### Tabela dos dados do Dataset 1, contendo todos os atributos.

In [24]:
ST_df

having_IP_Address URL_Length Shortining_Service having_At_Symbol  \
0                    -1          1                  1                1   
1                     1          1                  1                1   
2                     1          0                  1                1   
3                     1          0                  1                1   
4                     1          0                 -1                1   
...                 ...        ...                ...              ...   
11050                 1         -1                  1               -1   
11051                -1          1                  1               -1   
11052                 1         -1                  1                1   
11053                -1         -1                  1                1   
11054                -1         -1                  1                1   

      double_slash_redirecting Prefix_Suffix having_Sub_Domain SSLfinal_State  \
0                           -1            -1                -1             -1   
1                            1            -1                 0              1   
2                            1            -1                -1             -1   
3                            1            -1                -1             -1   
4                            1            -1                 1              1   
...                        ...           ...               ...            ...   
11050                        1             1                 1              1   
11051                       -1            -1                 1             -1   
11052                        1            -1                 1             -1   
11053                        1            -1                -1             -1   
11054                        1            -1                -1             -1   

      Domain_registeration_length Favicon  ... popUpWidnow Iframe  \
0                              -1       1  ...           1      1   
1                              -1       1  ...           1      1   
2                              -1       1  ...           1      1   
3                               1       1  ...           1      1   
4                              -1       1  ...          -1      1   
...                           ...     ...  ...         ...    ...   
11050                          -1      -1  ...          -1     -1   
11051                          -1      -1  ...          -1      1   
11052                          -1       1  ...           1      1   
11053                           1      -1  ...          -1      1   
11054                           1       1  ...           1      1   

      age_of_domain DNSRecord web_traffic Page_Rank Google_Index  \
0                -1        -1          -1        -1            1   
1                -1        -1           0        -1            1   
2                 1        -1           1        -1            1   
3                -1        -1           1        -1            1   
4                -1        -1           0        -1            1   
...             ...       ...         ...       ...          ...   
11050             1         1          -1        -1            1   
11051             1         1           1         1            1   
11052             1         1           1        -1            1   
11053             1         1           1        -1            1   
11054            -1         1          -1        -1           -1   

      Links_pointing_to_page Statistical_report Result  
0                          1                 -1     -1  
1                          1                  1     -1  
2                          0                 -1     -1  
3                         -1                  1     -1  
4                          1                  1      1  
...                      ...                ...    ...  
11050                      1                  1      1  
11051                     -1              

### Tabela dos dados do Dataset 1, contendo os melhores atributos.

In [25]:
ST_df_best_features

having_IP_Address URL_Length Shortining_Service having_At_Symbol  \
0                    -1          1                  1                1   
1                     1          1                  1                1   
2                     1          0                  1                1   
3                     1          0                  1                1   
4                     1          0                 -1                1   
...                 ...        ...                ...              ...   
11050                 1         -1                  1               -1   
11051                -1          1                  1               -1   
11052                 1         -1                  1                1   
11053                -1         -1                  1                1   
11054                -1         -1                  1                1   

      Prefix_Suffix having_Sub_Domain SSLfinal_State  \
0                -1                -1             -1   
1                -1                 0              1   
2                -1                -1             -1   
3                -1                -1             -1   
4                -1                 1              1   
...             ...               ...            ...   
11050             1                 1              1   
11051            -1                 1             -1   
11052            -1                 1             -1   
11053            -1                -1             -1   
11054            -1                -1             -1   

      Domain_registeration_length Request_URL URL_of_Anchor Links_in_tags SFH  \
0                              -1           1            -1             1  -1   
1                              -1           1             0            -1  -1   
2                              -1           1             0            -1  -1   
3                               1          -1             0             0  -1   
4                              -1           1             0             0  -1   
...                           ...         ...           ...           ...  ..   
11050                          -1           1             1             1  -1   
11051                          -1           1            -1            -1   0   
11052                          -1           1             0            -1  -1   
11053                           1          -1            -1             1  -1   
11054                           1          -1            -1             0  -1   

      Abnormal_URL age_of_domain DNSRecord web_traffic Page_Rank Google_Index  \
0               -1            -1        -1          -1        -1            1   
1                1            -1        -1           0        -1            1   
2               -1             1        -1           1        -1            1   
3                1            -1        -1           1        -1            1   
4                1            -1        -1           0        -1            1   
...            ...           ...       ...         ...       ...          ...   
11050            1             1         1          -1        -1            1   
11051           -1             1         1           1         1            1   
11052            1             1         1           1        -1            1   
11053            1             1         1           1        -1            1   
11054            1            -1         1          -1        -1           -1   

      Statistical_report  Result  
0                     -1      -1  
1                      1      -1  
2                     -1      -1  
3                      1      -1  
4                      1       1  
...                  ...     ...  
11050                  1       1  
11051                  1      -1  
11052                  1      -1  
11053                  1      -1  
11054                 -1      -1  

[11055 rows x 20 columns]

In [26]:
# file_path = "trainingdataset.arff" # Dados: 11055
# file_path = "old.arff" # Dados: 2456
ND_df = pd.read_csv('fixed_values_ds.csv')

oversample2 = RandomUnderSampler(sampling_strategy='majority')

ND_df_best_features = ND_df.drop([
    'double-slash_redirection', 
    'favicons', 
    'ports', 
    'https', 
    'auto_email', 
    'iframe_redirection', 
    'on_mouse_over', 
    'right_click',
    'popup_windows', 
    'links_pointing', 
    'image_text_keyword'
], axis=1)
# ND_df_best_features

# ND_df['result'].value_counts()

### Tabela dos dados do Dataset 2, contendo todos os atributos.

In [27]:
ND_df

having_ip_address  length_of_url  shortening_services  \
0                     -1             -1                   -1   
1                     -1              0                   -1   
2                     -1             -1                   -1   
3                     -1             -1                   -1   
4                     -1              1                   -1   
...                  ...            ...                  ...   
14088                 -1             -1                   -1   
14089                 -1             -1                   -1   
14090                 -1             -1                   -1   
14091                 -1             -1                   -1   
14092                 -1             -1                   -1   

       having_at_symbol  double-slash_redirection  prefix and suffix  \
0                    -1                        -1                 -1   
1                    -1                        -1                  1   
2                    -1                        -1                 -1   
3                    -1                        -1                 -1   
4                    -1                        -1                  1   
...                 ...                       ...                ...   
14088                -1                        -1                 -1   
14089                -1                        -1                 -1   
14090                -1                        -1                 -1   
14091                -1                        -1                 -1   
14092                -1                        -1                 -1   

       sub_domains  ssl_state  domain_registered  favicons  ...  \
0                1          1                  1         1  ...   
1                0         -1                  1         1  ...   
2               -1         -1                  1         1  ...   
3               -1         -1                  1         1  ...   
4                1         -1                  1         1  ...   
...            ...        ...                ...       ...  ...   
14088            0         -1                  1        -1  ...   
14089            0         -1                  1        -1  ...   
14090            0         -1                  1        -1  ...   
14091            0         -1                  1        -1  ...   
14092            0         -1                  1        -1  ...   

       on_mouse_over  right_click  popup_windows  domain_age  dns_record  \
0                  1            1              1           1           1   
1                 -1           -1             -1          -1           1   
2                 -1           -1             -1          -1           1   
3                 -1           -1             -1          -1           1   
4                 -1           -1             -1           1           1   
...              ...          ...            ...         ...         ...   
14088             -1           -1             -1           1           1   
14089             -1           -1             -1          -1           1   
14090             -1           -1             -1          -1           1   
14091             -1           -1             -1          -1           1   
14092             -1           -1             -1          -1           1   

       web_traffic  links_pointing  statistical_report  image_text_keyword  \
0                1               1                  -1                  -1   
1                1              -1                  -1                   1   
2                1              -1                  -1                   1   
3                0              -1                  -1                   1   
4               -1              -1                  -1                  -1   
...            ...             ...                 ...                 ...   
14088           -1               1                  -1                   1   
14089           -1             

### Tabela dos dados do Dataset 2, contendo os melhores atributos.

In [28]:
ND_df_best_features

having_ip_address  length_of_url  shortening_services  \
0                     -1             -1                   -1   
1                     -1              0                   -1   
2                     -1             -1                   -1   
3                     -1             -1                   -1   
4                     -1              1                   -1   
...                  ...            ...                  ...   
14088                 -1             -1                   -1   
14089                 -1             -1                   -1   
14090                 -1             -1                   -1   
14091                 -1             -1                   -1   
14092                 -1             -1                   -1   

       having_at_symbol  prefix and suffix  sub_domains  ssl_state  \
0                    -1                 -1            1          1   
1                    -1                  1            0         -1   
2                    -1                 -1           -1         -1   
3                    -1                 -1           -1         -1   
4                    -1                  1            1         -1   
...                 ...                ...          ...        ...   
14088                -1                 -1            0         -1   
14089                -1                 -1            0         -1   
14090                -1                 -1            0         -1   
14091                -1                 -1            0         -1   
14092                -1                 -1            0         -1   

       domain_registered  external_objects  anchor_tags  links_in_tags  \
0                      1                -1           -1             -1   
1                      1                 1            1              1   
2                      1                 1            1              1   
3                      1                 1            1              1   
4                      1                 1           -1              1   
...                  ...               ...          ...            ...   
14088                  1                -1            1             -1   
14089                  1                 1           -1             -1   
14090                  1                -1            1              0   
14091                  1                 1           -1              0   
14092                  1                 1            1              0   

       sfh-domain  abnoramal_url  domain_age  dns_record  web_traffic  \
0               0              1           1           1            1   
1              -1             -1          -1           1            1   
2              -1             -1          -1           1            1   
3              -1             -1          -1           1            0   
4              -1             -1           1           1           -1   
...           ...            ...         ...         ...          ...   
14088          -1             -1           1           1           -1   
14089          -1             -1          -1           1           -1   
14090          -1             -1          -1           1           -1   
14091           0             -1          -1           1           -1   
14092          -1             -1          -1           1           -1   

       statistical_report  result  
0                      -1       1  
1                      -1       1  
2                      -1       1  
3                      -1       1  
4                      -1       1  
...                   ...     ...  
14088                  -1      -1  
14089                  -1      -1  
14090                  -1      -1  
14091                  -1      -1  
14092                  -1      -1  

[14093 rows x 18 columns]

## Random Forest (RF)

#### Dataset_1 + All_features

In [11]:
# #Atributo de saída
y_st = ST_df['Result'].values

# #Atributos de entrada
X_st = ST_df.drop('Result', axis=1)

X_st, y_st = oversample1.fit_resample(X_st, y_st)

X_st_train, X_st_test, y_st_train, y_st_test = train_test_split(X_st, y_st, test_size=0.3,random_state=42)

clf = RandomForestClassifier().fit(X_st_train, y_st_train)
y_pred = clf.predict(X_st_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_st_test, y_pred) * 100))
print(classification_report(y_st_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 96.60%

                precision    recall  f1-score   support

 Phishing (-1)     0.9730    0.9601    0.9665      1502
Legitimate (1)     0.9588    0.9722    0.9654      1437

      accuracy                         0.9660      2939
     macro avg     0.9659    0.9661    0.9660      2939
  weighted avg     0.9661    0.9660    0.9660      2939



#### Dataset_1 + Best_features

In [12]:
# #Atributo de saída
y_st = ST_df_best_features['Result'].values

# #Atributos de entrada
X_st = ST_df_best_features.drop('Result', axis=1)

X_st, y_st = oversample1.fit_resample(X_st, y_st)

X_st_train, X_st_test, y_st_train, y_st_test = train_test_split(X_st, y_st, test_size=0.3,random_state=42)

clf = RandomForestClassifier().fit(X_st_train, y_st_train)
y_pred = clf.predict(X_st_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_st_test, y_pred) * 100))
print(classification_report(y_st_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 95.54%

                precision    recall  f1-score   support

 Phishing (-1)     0.9641    0.9481    0.9560      1502
Legitimate (1)     0.9466    0.9631    0.9548      1437

      accuracy                         0.9554      2939
     macro avg     0.9554    0.9556    0.9554      2939
  weighted avg     0.9556    0.9554    0.9554      2939



#### Dataset_2 + All_features

In [13]:
# #Atributo de saída
y_nd = ND_df['result'].values

# #Atributos de entrada
X_nd = ND_df.drop('result', axis=1)

X_nd, y_nd = oversample2.fit_resample(X_nd, y_nd)

X_nd_train, X_nd_test, y_nd_train, y_nd_test = train_test_split(X_nd, y_nd, test_size=0.3,random_state=42)

clf = RandomForestClassifier().fit(X_nd_train, y_nd_train)
y_pred = clf.predict(X_nd_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_nd_test, y_pred) * 100))
print(classification_report(y_nd_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 92.03%

                precision    recall  f1-score   support

 Phishing (-1)     0.9273    0.9119    0.9196      2112
Legitimate (1)     0.9135    0.9286    0.9210      2115

      accuracy                         0.9203      4227
     macro avg     0.9204    0.9203    0.9203      4227
  weighted avg     0.9204    0.9203    0.9203      4227



#### Dataset_2 + Best_features

In [14]:
# #Atributo de saída
y_nd = ND_df_best_features['result'].values

# #Atributos de entrada
X_nd = ND_df_best_features.drop('result', axis=1)

X_nd, y_nd = oversample2.fit_resample(X_nd, y_nd)

X_nd_train, X_nd_test, y_nd_train, y_nd_test = train_test_split(X_nd, y_nd, test_size=0.3,random_state=42)

clf = RandomForestClassifier().fit(X_nd_train, y_nd_train)
y_pred = clf.predict(X_nd_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_nd_test, y_pred) * 100))
print(classification_report(y_nd_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 85.69%

                precision    recall  f1-score   support

 Phishing (-1)     0.8458    0.8726    0.8590      2112
Legitimate (1)     0.8687    0.8411    0.8547      2115

      accuracy                         0.8569      4227
     macro avg     0.8572    0.8569    0.8568      4227
  weighted avg     0.8572    0.8569    0.8568      4227



## Support Vector Machine (SVM)

#### Dataset_1 + All_features

In [15]:
# #Atributo de saída
y_st = ST_df['Result'].values

# #Atributos de entrada
X_st = ST_df.drop('Result', axis=1)

X_st, y_st = oversample1.fit_resample(X_st, y_st)

X_st_train, X_st_test, y_st_train, y_st_test = train_test_split(X_st, y_st, test_size=0.3,random_state=42)

svm_model = svm.SVC(kernel='linear').fit(X_st_train, y_st_train)
y_pred = svm_model.predict(X_st_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_st_test, y_pred) * 100))
print(classification_report(y_st_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 92.00%

                precision    recall  f1-score   support

 Phishing (-1)     0.9342    0.9075    0.9206      1502
Legitimate (1)     0.9061    0.9332    0.9194      1437

      accuracy                         0.9200      2939
     macro avg     0.9201    0.9203    0.9200      2939
  weighted avg     0.9205    0.9200    0.9200      2939



#### Dataset_1 + Best_features

In [16]:
# #Atributo de saída
y_st = ST_df_best_features['Result'].values

# #Atributos de entrada
X_st = ST_df_best_features.drop('Result', axis=1)

X_st, y_st = oversample1.fit_resample(X_st, y_st)

X_st_train, X_st_test, y_st_train, y_st_test = train_test_split(X_st, y_st, test_size=0.3,random_state=42)

svm_model = svm.SVC(kernel='linear').fit(X_st_train, y_st_train)
y_pred = svm_model.predict(X_st_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_st_test, y_pred) * 100))
print(classification_report(y_st_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 91.83%

                precision    recall  f1-score   support

 Phishing (-1)     0.9419    0.8955    0.9181      1502
Legitimate (1)     0.8961    0.9422    0.9186      1437

      accuracy                         0.9183      2939
     macro avg     0.9190    0.9189    0.9183      2939
  weighted avg     0.9195    0.9183    0.9183      2939



#### Dataset_2 + All_features

In [17]:
# #Atributo de saída
y_nd = ND_df['result'].values

# #Atributos de entrada
X_nd = ND_df.drop('result', axis=1)

X_nd, y_nd = oversample2.fit_resample(X_nd, y_nd)

X_nd_train, X_nd_test, y_nd_train, y_nd_test = train_test_split(X_nd, y_nd, test_size=0.3,random_state=42)

svm_model = svm.SVC(kernel='linear').fit(X_nd_train, y_nd_train)
y_pred = svm_model.predict(X_nd_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_nd_test, y_pred) * 100))
print(classification_report(y_nd_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 86.85%

                precision    recall  f1-score   support

 Phishing (-1)     0.9082    0.8196    0.8616      2112
Legitimate (1)     0.8358    0.9173    0.8747      2115

      accuracy                         0.8685      4227
     macro avg     0.8720    0.8684    0.8681      4227
  weighted avg     0.8720    0.8685    0.8681      4227



#### Dataset_2 + Best_features

In [18]:
# #Atributo de saída
y_nd = ND_df_best_features['result'].values

# #Atributos de entrada
X_nd = ND_df_best_features.drop('result', axis=1)

X_nd, y_nd = oversample2.fit_resample(X_nd, y_nd)

X_nd_train, X_nd_test, y_nd_train, y_nd_test = train_test_split(X_nd, y_nd, test_size=0.3,random_state=42)

svm_model = svm.SVC(kernel='linear').fit(X_nd_train, y_nd_train)
y_pred = svm_model.predict(X_nd_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_nd_test, y_pred) * 100))
print(classification_report(y_nd_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 81.57%

                precision    recall  f1-score   support

 Phishing (-1)     0.8351    0.7865    0.8100      2112
Legitimate (1)     0.7985    0.8449    0.8210      2115

      accuracy                         0.8157      4227
     macro avg     0.8168    0.8157    0.8155      4227
  weighted avg     0.8168    0.8157    0.8155      4227



## Logistic Regression (LR)

#### Dataset_1 + All_features

In [19]:
# #Atributo de saída
y_st = ST_df['Result'].values

# #Atributos de entrada
X_st = ST_df.drop('Result', axis=1)

X_st, y_st = oversample1.fit_resample(X_st, y_st)

X_st_train, X_st_test, y_st_train, y_st_test = train_test_split(X_st, y_st, test_size=0.3,random_state=42)

clf = LogisticRegression().fit(X_st_train, y_st_train)
y_pred = clf.predict(X_st_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_st_test, y_pred) * 100))
print(classification_report(y_st_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 92.45%

                precision    recall  f1-score   support

 Phishing (-1)     0.9444    0.9055    0.9245      1502
Legitimate (1)     0.9053    0.9443    0.9244      1437

      accuracy                         0.9245      2939
     macro avg     0.9249    0.9249    0.9245      2939
  weighted avg     0.9253    0.9245    0.9245      2939



#### Dataset_1 + Best_features

In [20]:
# #Atributo de saída
y_st = ST_df_best_features['Result'].values

# #Atributos de entrada
X_st = ST_df_best_features.drop('Result', axis=1)

X_st, y_st = oversample1.fit_resample(X_st, y_st)

X_st_train, X_st_test, y_st_train, y_st_test = train_test_split(X_st, y_st, test_size=0.3,random_state=42)

clf = LogisticRegression().fit(X_st_train, y_st_train)
y_pred = clf.predict(X_st_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_st_test, y_pred) * 100))
print(classification_report(y_st_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 92.24%

                precision    recall  f1-score   support

 Phishing (-1)     0.9492    0.8961    0.9219      1502
Legitimate (1)     0.8974    0.9499    0.9229      1437

      accuracy                         0.9224      2939
     macro avg     0.9233    0.9230    0.9224      2939
  weighted avg     0.9239    0.9224    0.9224      2939



#### Dataset_2 + All_features

In [39]:
# #Atributo de saída
y_nd = ND_df['result'].values

# #Atributos de entrada
X_nd = ND_df.drop('result', axis=1)

X_nd, y_nd = oversample2.fit_resample(X_nd, y_nd)

X_nd_train, X_nd_test, y_nd_train, y_nd_test = train_test_split(X_nd, y_nd, test_size=0.3,random_state=42)

clf = LogisticRegression(max_iter=300).fit(X_nd_train, y_nd_train)
y_pred = clf.predict(X_nd_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_nd_test, y_pred) * 100))
print(classification_report(y_nd_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 83.56%

                precision    recall  f1-score   support

 Phishing (-1)     0.8428    0.8248    0.8337      2112
Legitimate (1)     0.8287    0.8463    0.8374      2115

      accuracy                         0.8356      4227
     macro avg     0.8357    0.8356    0.8356      4227
  weighted avg     0.8357    0.8356    0.8356      4227



#### Dataset_2 + Best_features

In [22]:
# #Atributo de saída
y_nd = ND_df_best_features['result'].values

# #Atributos de entrada
X_nd = ND_df_best_features.drop('result', axis=1)

X_nd, y_nd = oversample2.fit_resample(X_nd, y_nd)

X_nd_train, X_nd_test, y_nd_train, y_nd_test = train_test_split(X_nd, y_nd, test_size=0.3,random_state=42)

clf = LogisticRegression().fit(X_nd_train, y_nd_train)
y_pred = clf.predict(X_nd_test)

print("Accuracy: %.2f%%\n" % (accuracy_score(y_nd_test, y_pred) * 100))
print(classification_report(y_nd_test, y_pred, target_names=['Phishing (-1)', 'Legitimate (1)'], digits=4))

Accuracy: 81.12%

                precision    recall  f1-score   support

 Phishing (-1)     0.8135    0.8073    0.8104      2112
Legitimate (1)     0.8090    0.8151    0.8121      2115

      accuracy                         0.8112      4227
     macro avg     0.8112    0.8112    0.8112      4227
  weighted avg     0.8112    0.8112    0.8112      4227

